# Прогнозирование статуса студента

**Задача**

На основе данных об абитуриенте необходимо предсказать:


*   продолжит ли студент обучение
*   отчислится
*  возьмет академический отпуск


**Метрика в соревновании:**

F1

## Импорты

Импортируем библиотеки и модули, которые нам понадобятся

In [1]:
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import plotly.express as px
from statistics import mode

from sklearn.model_selection import train_test_split, cross_val_score
from sklearn import tree
import numpy as np
from sklearn.metrics import f1_score

import numpy as np 
from sklearn.utils.class_weight import compute_class_weight

from catboost import CatBoostClassifier
from catboost import cv, Pool

%matplotlib inline

Зафиксируем RANDOM STATE

In [ ]:
RANDOM_STATE = 42

## Первичный анализ данных

Загрузим тренировочный и тестовый датасеты

In [ ]:
df = pd.read_csv("/content/train.csv")

In [ ]:
test_df = pd.read_csv('/content/test.csv')

Посмотрим на первые строки в датасетах

In [ ]:
df.head(10)

ID  Код_группы  Год_Поступления  Пол Основания   Изучаемый_Язык  \
0  72716       16019             2015  Жен        ОО  Английский язык   
1  63306       14895             2010  Муж        ЦН              NaN   
2  82469       20103             2017  Жен        ДН  Английский язык   
3  81661       19838             2017  Жен        БН  Английский язык   
4  81509       19803             2017  Жен        БН  Английский язык   
5  72669       18733             2015  Муж        СН  Английский язык   
6  57717       16945             2013  Муж        СН              NaN   
7  65208       18196             2014  Жен        СН  Английский язык   
8  78608       19620             2016  Жен        СН  Английский язык   
9  83857       19966             2017  Муж        ОО  Английский язык   

             Дата_Рождения                                    Уч_Заведение  \
0  1998-02-08 00:00:00.000                                  МБОУ "СОШ №59"   
1  1992-04-18 00:00:00.000                                             NaN   
2  1999-03-21 00:00:00.000                           МБОУ Алтайская СОШ №5   
3  1994-12-08 00:00:00.000  ФГБОУ ВО Алтайский государственный университет   
4  1995-06-28 00:00:00.000  ФГБОУ ВО Алтайский государственный университет   
5  1997-11-13 00:00:00.000                                 МБОУ "СОШ №110"   
6  1995-05-10 00:00:00.000                                             NaN   
7  1996-05-20 00:00:00.000                           МБОУ "Калманская СОШ"   
8  1994-09-05 00:00:00.000  ФГБОУ ВО Алтайский государственный университет   
9  1999-06-24 00:00:00.000                                 МБОУ Лицей №101   

                             Где_Находится_УЗ  Год_Окончания_УЗ  ...  \
0                   Алтайский край, Барнаул г            2014.0  ...   
1                                         NaN               NaN  ...   
2  Алтайский край, Алтайский р-н, Алтайское с            2017.0  ...   
3                  Алтайский край, г. Барнаул            2017.0  ...   
4                  Алтайский край, г. Барнаул            2017.0  ...   
5                   Алтайский край, Барнаул г            2015.0  ...   
6                                         NaN               NaN  ...   
7  Алтайский край, Калманский р-н, Калманка с            2014.0  ...   
8           Россия, Алтайский край, г Барнаул            2016.0  ...   
9                  Алтайский край, г. Барнаул            2017.0  ...   

   Общежитие Наличие_Матери Наличие_Отца Страна_Родители  Опекунство  Село  \
0        0.0              0          0.0          Россия         0.0   0.0   
1        0.0              1          1.0          Россия         0.0   0.0   
2        0.0              1          1.0          Россия         0.0   0.0   
3        0.0              1          1.0          Россия         0.0   0.0   
4        0.0              1          1.0          Россия         0.0   0.0   
5        0.0              0          0.0          Россия         0.0   0.0   
6        0.0              1          1.0             NaN         0.0   0.0   
7        1.0              0          0.0          Россия         0.0   1.0   
8        0.0              1          1.0          Россия         0.0   0.0   
9        0.0              1          1.0          Россия         0.0   0.0   

   Иностранец КодФакультета  СрБаллАттестата  Статус  
0         0.0          41.0            4.294       3  
1         0.0          28.0           67.000       4  
2         0.0          41.0            4.133       4  
3         0.0          35.0           74.000       4  
4         0.0          28.0           53.000       4  
5         0.0          41.0            3.692       3  
6         0.0          51.0           67.000       4  
7         0.0          51.0           58.000       3  
8         0.0          26.0           78.000       4  
9         0.0          34.0           65.000       3  

[10 rows x 24 columns]

In [ ]:
test_df.head(10)

ID  Код_группы  Год_Поступления  Пол Основания   Изучаемый_Язык  \
0  64996       20608             2014  Жен        ДН  Английский язык   
1  71837       20613             2015  Жен        ДН    Немецкий язык   
2  86587       21210             2018  Жен        ОО  Английский язык   
3  73673       22254             2015  Жен        ОО  Английский язык   
4  54709       15040             2012  Жен        ОО              NaN   
5  56072       13529             2013  Жен        ОО  Английский язык   
6  77774       18616             2016  Жен        СН  Английский язык   
7  90707       21922             2019  Жен        ОО  Английский язык   
8  76202       20723             2016  Жен        ДН  Английский язык   
9  74726       20664             2016  Жен        БН  Английский язык   

             Дата_Рождения                                       Уч_Заведение  \
0  1995-11-03 00:00:00.000                                     МБОУ "СОШ №55"   
1  1995-12-10 00:00:00.000                                      МБОУ "СОШ №1"   
2  1973-08-09 00:00:00.000  Алтайский государственный медицинский университет   
3  1983-12-07 00:00:00.000    ГОУ ВПО "Алтайский государственный университет"   
4  1994-05-21 00:00:00.000                                                NaN   
5  1990-12-03 00:00:00.000  ФГБОУ ВПО "Алтайский государственный университет"   
6  1981-11-30 00:00:00.000  Бийский педагогический государственный универс...   
7  1997-02-28 00:00:00.000  ФГБОУ ВО Алтайский государственный технический...   
8  1998-09-02 00:00:00.000                               МБОУ Троицкая СОШ №2   
9  1999-05-11 00:00:00.000                              МОУ Эликманарская СОШ   

                                    Где_Находится_УЗ  Год_Окончания_УЗ  ...  \
0                          Алтайский край, Барнаул г            2014.0  ...   
1                         Алтайский край, Рубцовск г            2014.0  ...   
2                         Алтайский край, г. Барнаул            1997.0  ...   
3                          Алтайский край, Барнаул г            2006.0  ...   
4                                                NaN               NaN  ...   
5                                            Барнаул            2013.0  ...   
6                    Россия, Алтайский край, г Бийск            2003.0  ...   
7                         Алтайский край, г. Барнаул            2019.0  ...   
8   Россия, Алтайский край, Троицкий р-н, с Троицкое            2016.0  ...   
9  Россия, Республика Алтай, Чемальский р-н, с Эл...            2016.0  ...   

         Город_ПП Общежитие Наличие_Матери Наличие_Отца  Страна_Родители  \
0       Барнаул г       0.0              0          0.0           Россия   
1      Барнаул  г       0.0              0          0.0           Россия   
2      г. Барнаул       0.0              1          1.0           Россия   
3       Барнаул г       0.0              0          0.0           Россия   
4             NaN       0.0              1          1.0           Россия   
5  г. Новоалтайск       0.0              0          0.0           Россия   
6      Белокуриха       0.0              1          1.0           Россия   
7  им Мамонтова п       0.0              0          0.0           Россия   
8             NaN       0.0              1          1.0           Россия   
9          Аюла с       0.0              1          1.0           Россия   

   Опекунство  Село Иностранец  КодФакультета  СрБаллАттестата  
0         0.0   0.0        0.0           40.0             49.0  
1         0.0   1.0        0.0           26.0             77.0  
2         0.0   0.0        0.0           34.0             74.0  
3         0.0   0.0        0.0           53.0             57.0  
4         0.0   0.0        0.0           36.0             55.0  
5         0.0   0.0        0.0           28.0             92.0  
6         0.0   0.0        0.0           26.0             56.0  
7         0.0   1.0        0.0           27.0             58.0  
8         0.0   0.

Выведем размеры датасетов

In [ ]:
df.shape

(13584, 24)

In [ ]:
test_df.shape

(6691, 23)

Посмотрим общую информацию о таблицах

In [ ]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 13584 entries, 0 to 13583
Data columns (total 24 columns):
 #   Column            Non-Null Count  Dtype  
---  ------            --------------  -----  
 0   ID                13584 non-null  int64  
 1   Код_группы        13584 non-null  int64  
 2   Год_Поступления   13584 non-null  int64  
 3   Пол               13577 non-null  object 
 4   Основания         13584 non-null  object 
 5   Изучаемый_Язык    12758 non-null  object 
 6   Дата_Рождения     13584 non-null  object 
 7   Уч_Заведение      12351 non-null  object 
 8   Где_Находится_УЗ  12203 non-null  object 
 9   Год_Окончания_УЗ  12284 non-null  float64
 10  Пособие           12576 non-null  float64
 11  Страна_ПП         13237 non-null  object 
 12  Регион_ПП         12966 non-null  object 
 13  Город_ПП          13141 non-null  object 
 14  Общежитие         13498 non-null  float64
 15  Наличие_Матери    13584 non-null  int64  
 16  Наличие_Отца      13584 non-null  float6

In [ ]:
test_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6691 entries, 0 to 6690
Data columns (total 23 columns):
 #   Column            Non-Null Count  Dtype  
---  ------            --------------  -----  
 0   ID                6691 non-null   int64  
 1   Код_группы        6691 non-null   int64  
 2   Год_Поступления   6691 non-null   int64  
 3   Пол               6688 non-null   object 
 4   Основания         6691 non-null   object 
 5   Изучаемый_Язык    6295 non-null   object 
 6   Дата_Рождения     6691 non-null   object 
 7   Уч_Заведение      6113 non-null   object 
 8   Где_Находится_УЗ  6031 non-null   object 
 9   Год_Окончания_УЗ  6074 non-null   float64
 10  Пособие           6207 non-null   float64
 11  Страна_ПП         6531 non-null   object 
 12  Регион_ПП         6401 non-null   object 
 13  Город_ПП          6477 non-null   object 
 14  Общежитие         6656 non-null   float64
 15  Наличие_Матери    6691 non-null   int64  
 16  Наличие_Отца      6691 non-null   float64


Итак, в наших данных есть 22 столбца с фичами. В части столбцов есть пропущенные значения, а так же несоотвествие типов данных

## Предобработка

Посмотрим на количество пропусков в данных

In [ ]:
df.isna().sum()

ID                     0
Код_группы             0
Год_Поступления        0
Пол                    7
Основания              0
Изучаемый_Язык       826
Дата_Рождения          0
Уч_Заведение        1233
Где_Находится_УЗ    1381
Год_Окончания_УЗ    1300
Пособие             1008
Страна_ПП            347
Регион_ПП            618
Город_ПП             443
Общежитие             86
Наличие_Матери         0
Наличие_Отца           0
Страна_Родители      458
Опекунство             0
Село                  86
Иностранец           310
КодФакультета          0
СрБаллАттестата        0
Статус                 0
dtype: int64

In [ ]:
test_df.isna().sum()

ID                    0
Код_группы            0
Год_Поступления       0
Пол                   3
Основания             0
Изучаемый_Язык      396
Дата_Рождения         0
Уч_Заведение        578
Где_Находится_УЗ    660
Год_Окончания_УЗ    617
Пособие             484
Страна_ПП           160
Регион_ПП           290
Город_ПП            214
Общежитие            35
Наличие_Матери        0
Наличие_Отца          0
Страна_Родители     198
Опекунство            0
Село                 37
Иностранец          130
КодФакультета         0
СрБаллАттестата       0
dtype: int64

Далее рассмотрим каждый столбец отдельно

### ID 

Проверим, что все значения в столбце ID уникальные

In [ ]:
df['ID'].value_counts()

72716    1
83826    1
70095    1
88013    1
76114    1
        ..
48789    1
77819    1
70355    1
68700    1
80923    1
Name: ID, Length: 13584, dtype: int64

Поскольку value_counts по умолчанию сортирует значения по убыванию, то в столбце ID действительно все значения уникальные

### Код_группы

Посмотрим, какие значения встречаются в столбце 'Код группы' и сколько там уникальных значений

In [ ]:
df['Код_группы'].value_counts()

14705    23
20657    23
20698    22
20939    22
18540    21
         ..
21042     1
18176     1
20349     1
15053     1
13320     1
Name: Код_группы, Length: 3653, dtype: int64

In [ ]:
test_df['Код_группы'].value_counts()

20653    15
19437    13
17041    13
20650    13
15537    13
         ..
15935     1
15439     1
18502     1
17215     1
17837     1
Name: Код_группы, Length: 2677, dtype: int64

Поскольку номер группы - это не число, чтобы алгоритм не воспринимал значение порядковым, поменяем тип данных на category

In [ ]:
df['Код_группы'] = df['Код_группы'].astype('category')

In [ ]:
test_df['Код_группы'] = test_df['Код_группы'].astype('category')

### Год_Поступления

Посмотрим, какие значения встречаются в столбце 'Год_поступления'

In [ ]:
df['Год_Поступления'].value_counts()

2015    2353
2014    2290
2016    2271
2013    2070
2017    1460
2012    1394
2018    1147
2019     466
2020      48
2011      46
2010      19
2009       8
2007       5
2008       2
2212       1
2001       1
2004       1
2005       1
2003       1
Name: Год_Поступления, dtype: int64

In [ ]:
fig = px.box(df, y="Год_Поступления")
fig.show()

Видим явный выброс - 2212 год поступления. Скорее всего, имелся в виду 2012 год

In [ ]:
df.loc[df['Год_Поступления'] == 2212, 'Год_Поступления'] = 2012

Теперь оценим распределение

In [ ]:
fig = px.histogram(df, x="Год_Поступления")
fig.show()

Видим, что в среднем данные нормально распределены вокруг 2015 года. Но встречаются редкие значения вокруг 2005

Оценим тестовый датасет

In [ ]:
test_df['Год_Поступления'].value_counts()

2014    1177
2015    1172
2016    1114
2013    1028
2017     714
2012     637
2018     544
2019     227
2020      39
2011      23
2010       8
2009       5
2007       2
2006       1
Name: Год_Поступления, dtype: int64

В тестовых данных в этом столбце выбросов нет. Посомотрим на распределение

In [ ]:
fig = px.histogram(test_df, x="Год_Поступления")
fig.show()

Видим, что распределения в двух таблицах похожи

### Пол               

Посмотрим, нет ли аномалий в столбце с полом

In [ ]:
df['Пол'].value_counts()

Жен    8133
Муж    5443
муж       1
Name: Пол, dtype: int64

Заменим значение 'муж' на 'Муж'

In [ ]:
df.loc[df['Пол'] == 'муж', 'Пол'] = 'Муж'

Посмотрим на строки с пропуском в этом столбце

In [ ]:
df[df['Пол'].isna()]

ID Код_группы  Год_Поступления  Пол Основания   Изучаемый_Язык  \
1734   73266      17194             2015  NaN        СН  Английский язык   
2322   73100      16008             2015  NaN        ДН  Английский язык   
4235   78537      18499             2016  NaN        СН  Английский язык   
5864   78550      18499             2016  NaN        СН  Английский язык   
9881   86343      21006             2018  NaN        БН              NaN   
12448  78546      18499             2016  NaN        СН  Английский язык   
13271  65907      15447             2014  NaN        СН  Английский язык   

                 Дата_Рождения  \
1734   1994-11-22 00:00:00.000   
2322   1995-11-08 00:00:00.000   
4235   1996-07-03 00:00:00.000   
5864   1996-03-04 00:00:00.000   
9881   1997-03-15 00:00:00.000   
12448  1996-10-25 00:00:00.000   
13271  1983-08-20 00:00:00.000   

                                            Уч_Заведение  \
1734                                             СШ № 37   
2322                 средняя школа № 1 города Муданьцзян   
4235      Средняя школа уезда Наньсянь провинции Сычуань   
5864                      Средняя школа №8 города Далянь   
9881   Восточно-Казахстанский государственный универс...   
12448                                 СШ № 4 г. Цзиньчан   
13271    Синцзянский финансово-экономический университет   

                                        Где_Находится_УЗ  Год_Окончания_УЗ  \
1734                                      Китай, Аньян г            2015.0   
2322                                Китай, Муданьцзян г.            2013.0   
4235    Китай, провинция Сычуань, городской округ Мяньян            2014.0   
5864                                     Китай, г Далянь            2014.0   
9881   Казахстан, Восточно-Казахстанская область, г. ...            2018.0   
12448  Китай, провинция Ганьсу, городской округ Цзиньчан            2014.0   
13271                                   Китай, Синьцзянь            2007.0   

       ...  Общежитие Наличие_Матери Наличие_Отца Страна_Родители  Опекунство  \
1734   ...        1.0              0          0.0           Китай         0.0   
2322   ...        1.0              0          0.0           Китай         0.0   
4235   ...        1.0              1          1.0           Китай         0.0   
5864   ...        1.0              1          1.0           Китай         0.0   
9881   ...        1.0              1          1.0       Казахстан         0.0   
12448  ...        1.0              1          1.0           Китай         0.0   
13271  ...        1.0              0          0.0             КНР         0.0   

       Село  Иностранец КодФакультета  СрБаллАттестата  Статус  
1734    0.0         1.0          24.0             45.0       3  
2322    0.0         1.0          51.0             46.0       3  
4235    0.0         1.0          24.0             40.0       3  
5864    0.0         1.0          24.0             40.0       4  
9881    0.0         1.0          27.0             70.0       4  
12448   0.0         1.0          24.0             42.0       3  
13271   0.0         1.0          24.0             78.0       4  

[7 rows x 24 columns]

Общего между ними только то, что они все являются иностранцами. Поскольку данных, имеющихся у нас, недостаточно для точного определения пола, заполним пропуски нулями

In [ ]:
df['Пол'] = df['Пол'].fillna('0')

Выполним аналогичнные действия для тестового датафрейма

In [ ]:
test_df['Пол'].value_counts()

Жен    3974
Муж    2713
жен       1
Name: Пол, dtype: int64

In [ ]:
test_df.loc[test_df['Пол'] == 'жен', 'Пол'] = 'Жен'

In [ ]:
test_df['Пол'] = test_df['Пол'].fillna('0')

Посмотрим на распределения

In [ ]:
fig = px.histogram(df, x="Пол")
fig.show()

In [ ]:
fig = px.histogram(test_df, x="Пол")
fig.show()

Видим, что распределения относительно похожи

### Основания

Изучим, какие значения встречаются в стольце 'Основания'

In [ ]:
df['Основания'].value_counts()

ОО    5084
СН    4558
БН    1882
ДН    1853
ЦН     207
Name: Основания, dtype: int64

In [ ]:
test_df['Основания'].value_counts()

ОО    2565
СН    2177
ДН     972
БН     873
ЦН     103
ЛН       1
Name: Основания, dtype: int64

Видим странное значение ЛН. Поскольку, к букве Л на клавиатуре одинаково близко расположены, как буква Д, так и буква Б, выберем одну из них и заменим выброс

In [ ]:
test_df.loc[test_df['Основания'] == 'ЛН', 'Основания'] = 'ДН'

Посмотрим на распрделения

In [ ]:
fig = px.histogram(df, x="Основания")
fig.show()

In [ ]:
fig = px.histogram(test_df, x="Основания")
fig.show()

Видим, что в целом распределения схожи

### Изучаемый_Язык    

Поскольку поле с изучаемым языком заполнялось вручную, в нём, вероятно, будут опечатки или дубли. 

In [ ]:
df['Изучаемый_Язык'].value_counts()

Английский язык                  10450
Немецкий язык                     2219
Французский язык                    54
Русский язык                        11
Иностранный язык (Английский)       10
Англиийский                         10
Иностранный язык (Немецкий)          4
Name: Изучаемый_Язык, dtype: int64

Приведём все значения к единому виду

In [ ]:
df.loc[df['Изучаемый_Язык'] == 'Английский язык', 'Изучаемый_Язык'] = 'Английский'

In [ ]:
df.loc[df['Изучаемый_Язык'] == 'Англиийский', 'Изучаемый_Язык'] = 'Английский'

In [ ]:
df.loc[df['Изучаемый_Язык'] == 'Иностранный язык (Английский)', 'Изучаемый_Язык'] = 'Английский'

In [ ]:
df.loc[df['Изучаемый_Язык'] == 'Англиийский', 'Изучаемый_Язык'] = 'Английский'

In [ ]:
df.loc[df['Изучаемый_Язык'] == 'Немецкий язык', 'Изучаемый_Язык'] = 'Немецкий'

In [ ]:
df.loc[df['Изучаемый_Язык'] == 'Французский язык', 'Изучаемый_Язык'] = 'Французский'

In [ ]:
df.loc[df['Изучаемый_Язык'] == 'Русский язык', 'Изучаемый_Язык'] = 'Русский'

In [ ]:
df.loc[df['Изучаемый_Язык'] == 'Иностранный язык (Немецкий)', 'Изучаемый_Язык'] = 'Немецкий'

In [ ]:
df['Изучаемый_Язык'].value_counts()

Английский     11296
Немецкий        2223
Французский       54
Русский           11
Name: Изучаемый_Язык, dtype: int64

Поскольку английский язык встречается сильно больше остальных, заполним пропуски на 'Англиийский'

In [ ]:
df['Изучаемый_Язык'] = df['Изучаемый_Язык'].fillna('Англиийский')

Проделаем аналогичную работу для тестового датафрейма

In [ ]:
test_df['Изучаемый_Язык'].value_counts()

Английский язык                  5202
Немецкий язык                    1047
Французский язык                   28
Англиийский                         8
Иностранный язык (Английский)       8
Русский язык                        1
Английский, немецкий языки          1
Name: Изучаемый_Язык, dtype: int64

In [ ]:
test_df.loc[test_df['Изучаемый_Язык'] == 'Английский язык', 'Изучаемый_Язык'] = 'Английский'

In [ ]:
test_df.loc[test_df['Изучаемый_Язык'] == 'Англиийский', 'Изучаемый_Язык'] = 'Английский'

In [ ]:
test_df.loc[test_df['Изучаемый_Язык'] == 'Немецкий язык', 'Изучаемый_Язык'] = 'Немецкий'

In [ ]:
test_df.loc[test_df['Изучаемый_Язык'] == 'Французский язык', 'Изучаемый_Язык'] = 'Французский'

In [ ]:
test_df.loc[test_df['Изучаемый_Язык'] == 'Иностранный язык (Английский)', 'Изучаемый_Язык'] = 'Английский'

In [ ]:
test_df.loc[test_df['Изучаемый_Язык'] == 'Английский, немецкий языки', 'Изучаемый_Язык'] = 'Немецкий'

In [ ]:
test_df.loc[test_df['Изучаемый_Язык'] == 'Русский язык', 'Изучаемый_Язык'] = 'Русский'

In [ ]:
test_df['Изучаемый_Язык'].value_counts()

Английский     5614
Немецкий       1048
Французский      28
Русский           1
Name: Изучаемый_Язык, dtype: int64

In [ ]:
test_df['Изучаемый_Язык'] = test_df['Изучаемый_Язык'].fillna('Англиийский')

Оценим получившиеся распределения

In [ ]:
fig = px.histogram(df, x="Изучаемый_Язык")
fig.show()

In [ ]:
fig = px.histogram(test_df, x="Изучаемый_Язык")
fig.show()

### Дата_Рождения

Посмотрим, как в таблице представлена дата рождения

In [ ]:
df['Дата_Рождения'].head(3)

0    1998-02-08 00:00:00.000
1    1992-04-18 00:00:00.000
2    1999-03-21 00:00:00.000
Name: Дата_Рождения, dtype: object

Приведём столбец к типу datetime и вычленим год, месяц и число как отдельные фичи

In [ ]:
df['Дата_Рождения'] =  pd.to_datetime(df['Дата_Рождения'], format='%Y-%m-%d')

In [ ]:
df['Год_Рождения'] = df['Дата_Рождения'].dt.year

In [ ]:
df['Месяц_Рождения'] = df['Дата_Рождения'].dt.month

In [ ]:
df['Число_Рождения'] = df['Дата_Рождения'].dt.day

In [ ]:
test_df['Дата_Рождения'] =  pd.to_datetime(test_df['Дата_Рождения'], format='%Y-%m-%d')

In [ ]:
test_df['Год_Рождения'] = test_df['Дата_Рождения'].dt.year

In [ ]:
test_df['Месяц_Рождения'] = test_df['Дата_Рождения'].dt.month

In [ ]:
test_df['Число_Рождения'] = test_df['Дата_Рождения'].dt.day

Возможно, имелось в виду 2003 и 2002. Так будет чуть более правдоподобно

Теперь проверим на выбросы

In [ ]:
df['Год_Рождения'].value_counts()

1995    1959
1996    1812
1994    1771
1997    1548
1998    1251
1993     884
1999     668
1992     599
2000     454
1991     385
1990     290
2001     254
1989     187
1988     167
1987     154
1983     107
1984     105
1986     104
1985     101
1981      80
1980      76
2002      63
1982      62
1979      58
1977      57
1978      55
1975      47
1973      32
1976      32
1974      31
2003      26
1972      26
1971      22
1969      19
1970      17
1966      10
1967      10
2004       9
1968       9
1965       8
1964       7
1962       5
1963       5
1961       3
1960       3
1959       2
1957       2
1946       2
2013       1
2012       1
1951       1
2005       1
1949       1
1958       1
Name: Год_Рождения, dtype: int64

In [ ]:
fig = px.box(df, y="Год_Рождения")
fig.show()

2012 год рождения выглядит странно, как и 2013. Рассмотрим эти строки подробнее

In [ ]:
df[df['Год_Рождения'] > 2006]

ID Код_группы  Год_Поступления  Пол Основания Изучаемый_Язык  \
1470  70617      15794             2015  Жен        ДН       Немецкий   
4870  49234      11862             2013  Муж        ОО     Английский   

     Дата_Рождения                                       Уч_Заведение  \
1470    2013-03-16  ФГБОУ ВПО "Алтайский государственный техническ...   
4870    2012-06-26                          МБОУ "СОШ №7" г. Рубцовск   

               Где_Находится_УЗ  Год_Окончания_УЗ  ...  Страна_Родители  \
1470  Алтайский край, Барнаул г            2015.0  ...           Россия   
4870  г. Барнаул Алтайский край            2012.0  ...           Россия   

     Опекунство Село Иностранец  КодФакультета  СрБаллАттестата  Статус  \
1470        0.0  1.0        0.0           25.0             57.0       3   
4870        0.0  0.0        0.0           27.0             68.0       3   

     Год_Рождения  Месяц_Рождения  Число_Рождения  
1470         2013               3              16  
4870         2012               6              26  

[2 rows x 27 columns]

Возможно, предполагался 2002 и 2003 год рождения - так выглядит чуть более правдоподобно

In [ ]:
df.loc[df['Год_Рождения'] == 2012, 'Год_Рождения'] = 2002

In [ ]:
df.loc[df['Год_Рождения'] == 2013, 'Год_Рождения'] = 2003

In [ ]:
test_df['Год_Рождения'].value_counts()

1996    936
1995    934
1994    815
1997    746
1998    615
1993    431
1999    339
1992    305
2000    236
1991    216
1990    134
2001    126
1989    100
1987     85
1988     74
1985     64
1983     58
1986     48
1982     44
1984     43
2002     42
1981     32
1977     29
1980     28
1978     27
1973     20
1974     19
1976     18
1979     16
1975     16
1971     15
1970     11
2003     11
1972      9
1968      8
1960      8
1969      7
2004      4
1962      4
1967      4
1959      2
1966      2
2005      1
1965      1
1948      1
1964      1
1958      1
1963      1
1956      1
1950      1
1957      1
1961      1
Name: Год_Рождения, dtype: int64

In [ ]:
fig = px.box(test_df, y="Год_Рождения")
fig.show()

Явных выбросов нет

Посмотрим на месяц

In [ ]:
df['Месяц_Рождения'].value_counts()

3     1231
1     1194
5     1189
4     1186
6     1184
7     1179
8     1171
9     1110
12    1074
10    1059
2     1006
11    1001
Name: Месяц_Рождения, dtype: int64

In [ ]:
fig = px.box(df, y="Месяц_Рождения")
fig.show()

In [ ]:
test_df['Месяц_Рождения'].value_counts()

3     614
5     606
7     598
8     577
6     565
10    558
9     553
12    546
4     543
2     535
1     506
11    490
Name: Месяц_Рождения, dtype: int64

In [ ]:
fig = px.box(test_df, y="Месяц_Рождения")
fig.show()

И на число

In [ ]:
df['Число_Рождения'].value_counts()

12    482
6     480
16    475
10    473
22    468
24    465
7     464
20    461
19    458
14    458
17    456
23    454
11    453
15    452
4     451
28    448
18    443
26    439
9     438
27    438
8     435
1     434
5     430
2     427
30    423
25    422
13    412
29    406
3     402
21    393
31    244
Name: Число_Рождения, dtype: int64

In [ ]:
fig = px.box(df, y="Число_Рождения")
fig.show()

In [ ]:
test_df['Число_Рождения'].value_counts()

1     244
20    241
10    240
21    232
2     230
5     229
9     228
8     227
16    226
25    224
7     224
18    223
27    222
12    219
11    219
28    218
17    218
24    217
19    217
29    216
6     213
26    210
23    209
13    208
3     207
14    207
22    207
4     206
30    201
15    188
31    121
Name: Число_Рождения, dtype: int64

In [ ]:
fig = px.box(test_df, y="Число_Рождения")
fig.show()

Поскольку теперь у нас столбец Дата_Рождения преобразовался в три отдельных столбца, изначальный столбец можно удалить

In [ ]:
df = df.drop('Дата_Рождения', axis=1)

In [ ]:
test_df = test_df.drop('Дата_Рождения', axis=1)

### Уч_Заведение

Посмотрим, какие учебные заведения встречаются в датасетах

In [ ]:
df['Уч_Заведение'].value_counts()

ФГБОУ ВО Алтайский государственный университет                                   1359
ФГБОУ ВПО "Алтайский государственный университет"                                1025
ФГБОУ ВПО Алтайский государственный университет                                   113
ФГБОУ ВО Алтайский государственный технический университет им. И.И. Ползунова      88
Алтайский государственный университет                                              79
                                                                                 ... 
МБОУ "СОШ №89 с углублённым изучением отдельных предметов"                          1
МОУ"Солтонская СОШ"                                                                 1
МБОУ "Гимназия №3" г.Рубцовска Алтайский край                                       1
МБОУ СОШ №128                                                                       1
МКОУ "Георгиевская СОШ"                                                             1
Name: Уч_Заведение, Length: 3646, dtype: int64

Добавим доп фичи - из школы или из университета пришёл человек

In [ ]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 13584 entries, 0 to 13583
Data columns (total 26 columns):
 #   Column            Non-Null Count  Dtype   
---  ------            --------------  -----   
 0   ID                13584 non-null  int64   
 1   Код_группы        13584 non-null  category
 2   Год_Поступления   13584 non-null  int64   
 3   Пол               13584 non-null  object  
 4   Основания         13584 non-null  object  
 5   Изучаемый_Язык    13584 non-null  object  
 6   Уч_Заведение      12351 non-null  object  
 7   Где_Находится_УЗ  12203 non-null  object  
 8   Год_Окончания_УЗ  12284 non-null  float64 
 9   Пособие           12576 non-null  float64 
 10  Страна_ПП         13237 non-null  object  
 11  Регион_ПП         12966 non-null  object  
 12  Город_ПП          13141 non-null  object  
 13  Общежитие         13498 non-null  float64 
 14  Наличие_Матери    13584 non-null  int64   
 15  Наличие_Отца      13584 non-null  float64 
 16  Страна_Родители   1312

Заполним пропуски 0

In [ ]:
df['Уч_Заведение'] = df['Уч_Заведение'].fillna('0')

Для удобства приведём все записи к нижнему регистру

In [ ]:
df['Уч_Заведение'] = df['Уч_Заведение'].apply(lambda x: x.lower())

Сделаем столбец с типом учебного заведения

In [ ]:
df['Уч_Заведение_Тип'] = df['Уч_Заведение']

In [ ]:
def add_type_learn(x):
  if 'унив' in x or 'гу' in x or 'гту ' in x or 'алтгту' in x or 'агау' in x:
    return 'университет' 
  elif 'гимнази' in x or 'увк шг' in x:
    return 'гимназия'
  elif 'лице' in x or 'акпл' in x:
    return 'лицей'
  elif 'сош' in x or 'школ' in x or 'сш' in x or 'средн' in x or 'ош' in x or 'сомш' in x or 'ооу №' in x or 'схт' in x or 'сопш' in x or 'малышево-логовск' in x: 
    return 'школа'
  elif 'техникум' in x or 'пту' in x or 'пл-39' in x or 'ативт' in x:
    return 'техникум'
  elif 'колл' in x or 'ббмк' in x or 'ааск' in x:
    return 'колледж'
  elif 'академи' in x or 'ааэип' in x or 'ноу сга' in x:
    return 'академия'
  elif 'институт' in x or 'бюи' in x or 'взф' in x:
    return 'институт'
  elif 'училищ' in x or 'пу' in x:
    return 'училище'
  elif 'мбоу' in x or 'мбвоу' in x or 'моу' in x or 'мкоу' in x:
    return 'мбоу'
  elif 'соу' in x:
    return 'соу'
  elif 'фгбоу' in x:
    return 'фгбоу'
  elif 'спо' in x:
    return 'спо'
  elif 'консервато' in x:
    return 'консерватория'
  elif 'впо' in x:
    return 'впо'
  else:
    return '0'

In [ ]:
df['Уч_Заведение_Тип'] = df['Уч_Заведение_Тип'].apply(add_type_learn)

In [ ]:
df['Уч_Заведение_Тип'].value_counts(ascending=True)

консерватория       3
фгбоу               7
мбоу                8
спо                 9
впо                13
соу                42
училище           129
институт          169
техникум          230
академия          330
колледж           578
гимназия         1009
лицей            1085
0                1235
школа            4356
университет      4381
Name: Уч_Заведение_Тип, dtype: int64

Проведём аналогичную работу с тестовым датасетом

In [ ]:
test_df['Уч_Заведение'].value_counts()

ФГБОУ ВО Алтайский государственный университет                                   624
ФГБОУ ВПО "Алтайский государственный университет"                                532
ФГБОУ ВПО Алтайский государственный университет                                   60
ФГБОУ ВО Алтайский государственный технический университет им. И.И. Ползунова     47
МБОУ "Гимназия №42"                                                               40
                                                                                ... 
ФГБОУ ВО "Алтайский государственный университет" г. Барнаул                        1
КГБПОУ Бийский государствнный колледж                                              1
МБОУ "Ремзаводская СОШ" с. Павловск                                                1
СОУ №2                                                                             1
ГУ Павлодарский профессиональный лицей №7                                          1
Name: Уч_Заведение, Length: 2244, dtype: int64

Добавим доп фичи - из школы или из университета пришёл человек

In [ ]:
test_df['Уч_Заведение'] = test_df['Уч_Заведение'].fillna('0')

In [ ]:
test_df['Уч_Заведение'] = test_df['Уч_Заведение'].apply(lambda x: x.lower())

In [ ]:
test_df['Уч_Заведение_Тип'] = test_df['Уч_Заведение']

In [ ]:
def add_type_learn(x):
    if 'унив' in x or 'гу' in x or 'гту ' in x or 'алтгту' in x:
        return 'университет' 
    elif 'гимнази' in x or 'увк шг' in x or 'гамназия' in x:
        return 'гимназия'
    elif 'лице' in x or 'акпл' in x:
        return 'лицей'
    elif 'сош' in x or 'школ' in x or 'сш' in x or 'средн' in x or 'ош' in x or 'сомш' in x or 'ооу №' in x or 'схт' in x or 'сопш' in x or 'малышево-логовск' in x or 'гбоуш' in x or 'гаоу' in x: 
        return 'школа'
    elif 'техникум' in x or 'пту' in x or 'пл-39' in x or 'ативт' in x or 'чпоу нкт' in x or 'мтт' in x:
        return 'техникум'
    elif 'колл' in x or 'ббмк' in x or 'ааск' in x:
        return 'колледж'
    elif 'академи' in x or 'ааэип' in x or 'ноу сга' in x or 'аквдемия' in x:
        return 'академия'
    elif 'институт' in x or 'бюи' in x or 'взф' in x:
        return 'институт'
    elif 'училищ' in x or 'пу' in x:
        return 'училище'
    elif 'мбоу' in x or 'мбвоу' in x or 'моу' in x or 'мкоу' in x:
        return 'мбоу'
    elif 'соу' in x:
        return 'соу'
    elif 'фгбоу' in x:
        return 'фгбоу'
    elif 'нпо' in x:
        return 'нпо'
    elif 'спо' in x:
        return 'спо'
    elif 'консервато' in x:
        return 'консерватория'
    elif 'впо' in x:
        return 'впо'
    elif 'спн' in x:
        return 'спн'
    else:
        return x

In [ ]:
test_df['Уч_Заведение_Тип'] = test_df['Уч_Заведение_Тип'].apply(add_type_learn)

In [ ]:
test_df['Уч_Заведение_Тип'].value_counts(ascending=True)

консерватория       1
спо                 1
мбоу                3
впо                 5
фгбоу              11
соу                15
училище            58
институт          105
техникум          135
академия          159
колледж           260
гимназия          534
лицей             556
0                 578
школа            2132
университет      2138
Name: Уч_Заведение_Тип, dtype: int64

### Где_Находится_УЗ

In [ ]:
df['Где_Находится_УЗ'].value_counts()

Алтайский край, Барнаул г                         2413
Алтайский край, г. Барнаул                        1919
Россия, Алтайский край, г Барнаул                 1264
Алтайский край, Бийск г                            248
Алтайский край г. Барнаул                          228
                                                  ... 
с. Черёмушкино, Залесовского района                  1
г. Шемонаиха ВКО, реапублика Казахстан               1
Россия, Приморский край, г Находка                   1
Алтайский край, Бийс г                               1
Алтайский край, Ребрихинский р-н, Георгиевка с       1
Name: Где_Находится_УЗ, Length: 2110, dtype: int64

Заполним пропуски

In [ ]:
df['Где_Находится_УЗ'] = df['Где_Находится_УЗ'].fillna('0')

Теперь добавим столбец с городом учебного заведения

In [ ]:
df['Уч_Заведение_Город'] = df['Где_Находится_УЗ']

Приведём к нижнему регистру

In [ ]:
df['Уч_Заведение_Город'] = df['Уч_Заведение_Город'].apply(lambda x: x.lower())

In [ ]:
def add_city_learn(x):
    if 'барнаул' in x:
        return 'барнаул'
    elif 'бийск' in x:
        return 'бийск'
    elif 'горно-алтайск' in x:
        return 'горно-алтайск' 
    elif 'новоалтайск' in x:
        return 'новоалтайск'
    elif 'москв' in x:
        return 'москва'
    elif 'рубцовск' in x:
        return 'рубцовск'
    elif 'заринск' in x:
        return 'заринск'
    elif 'новосиб' in x:
        return 'новосибирск'
    elif 'камень' in x:
        return 'камень-на-оби'
    elif 'семей' in x:
        return 'семей'
    elif 'славгород' in x:
        return 'славгород'
    elif 'душанбе' in x:
        return 'душанбе'
    elif 'тальменка' in x:
        return 'тальменка'
    elif 'алейск' in x:
        return 'алейск'
    elif 'павловск' in x:
        return 'павловск'
    elif 'шемонаих' in x:
        return 'шемонаиха'
    elif 'волчих' in x:
        return 'волчиха'
    elif 'белокурих' in x:
        return 'белокуриха'
    elif 'поспелих' in x:
        return 'поспелиха'
    elif 'михайловск' in x:
        return 'михайловское'
    elif 'кулунда' in x:
        return 'кулунда'
    elif 'усть-каменогорск' in x:
        return 'усть-каменогорск'
    elif 'павлодар' in x:
        return 'павлодар'
    elif 'шипунов' in x:
        return 'шипуново'
    elif 'мамонтов' in x:
        return 'мамонтово'
    elif 'риддер' in x:
        return 'риддер'
    elif 'алтайское' in x:
        return 'алтайское'
    elif 'родин' in x:
        return 'родино'
    elif 'степное озер' in x:
        return 'степное озеро'
    elif 'томск' in x:
        return 'томск'
    elif 'топчих' in x:
        return 'топчиха'
    elif 'первомайск' in x:
        return 'первомайское'
    elif 'яров' in x:
        return 'яровое'
    elif 'сибирск' in x:
        return 'сибирский'
    elif 'троицк' in x:
        return 'троицкое'
    elif 'благовещенск' in x:
        return 'благовещенский'
    elif 'новичих' in x:
        return 'новичиха'
    elif 'налобих' in x:
        return 'налобиха'
    elif 'целинн' in x:
        return 'целинное'
    elif 'красногорск' in x:
        return 'красногорское'
    elif 'жалал-абад' in x:
        return 'жалал-абад'
    elif 'усть-калман' in x:
        return 'усть-калманка'
    elif 'залесов' in x:
        return 'залесово'
    elif 'ключ' in x:
        return 'ключи'
    elif 'тальменск' in x:
        return 'тальменский'
    elif 'курчатов' in x:
        return 'курчатов'
    else:
        return '0'

In [ ]:
df['Уч_Заведение_Город'] = df['Уч_Заведение_Город'].apply(add_city_learn)

In [ ]:
df['Уч_Заведение_Город'].value_counts().head(60)

барнаул             6790
0                   3215
бийск                580
горно-алтайск        218
новоалтайск          199
москва               167
рубцовск             152
заринск              137
павловск             132
новосибирск          122
камень-на-оби        122
славгород            111
семей                106
первомайское          93
алейск                86
шемонаиха             86
усть-каменогорск      85
павлодар              75
душанбе               67
риддер                61
белокуриха            60
шипуново              56
волчиха               52
поспелиха             49
тальменка             45
михайловское          44
троицкое              44
мамонтово             43
тальменский           43
сибирский             41
жалал-абад            40
топчиха               39
ключи                 39
благовещенский        37
усть-калманка         36
томск                 34
алтайское             33
родино                32
яровое                32
кулунда               32


Аналогично разберём тестовый датасет

In [ ]:
test_df['Где_Находится_УЗ'].value_counts()

Алтайский край, Барнаул г                            1237
Алтайский край, г. Барнаул                            945
Россия, Алтайский край, г Барнаул                     617
Барнаул                                               121
Алтайский край, Бийск г                               113
                                                     ... 
Алтайский край Алтайский р-на с. Старобелокуриха        1
Алтайский край с.Залесово                               1
Китай, провинция Гуандун, г Цинъюань, р-н Цинсинь       1
КНР, пров. Хубэй, уезд Дяньцзюань                       1
Алтайский край, Алейский р-н, Красный Яр с              1
Name: Где_Находится_УЗ, Length: 1260, dtype: int64

In [ ]:
test_df['Где_Находится_УЗ'] = test_df['Где_Находится_УЗ'].fillna('0')

In [ ]:
test_df['Уч_Заведение_Город'] = test_df['Где_Находится_УЗ']

In [ ]:
test_df['Уч_Заведение_Город'] = test_df['Уч_Заведение_Город'].apply(lambda x: x.lower())

In [ ]:
def add_city_learn(x):
    if 'барнаул' in x:
        return 'барнаул'
    elif 'бийск' in x:
        return 'бийск'
    elif 'горно-алтайск' in x:
        return 'горно-алтайск' 
    elif 'новоалтайск' in x:
        return 'новоалтайск'
    elif 'москв' in x:
        return 'москва'
    elif 'рубцовск' in x:
        return 'рубцовск'
    elif 'заринск' in x:
        return 'заринск'
    elif 'новосиб' in x:
        return 'новосибирск'
    elif 'камень' in x:
        return 'камень-на-оби'
    elif 'семей' in x:
        return 'семей'
    elif 'славгород' in x:
        return 'славгород'
    elif 'душанбе' in x:
        return 'душанбе'
    elif 'тальменка' in x:
        return 'тальменка'
    elif 'алейск' in x:
        return 'алейск'
    elif 'павловск' in x:
        return 'павловск'
    elif 'шемонаих' in x:
        return 'шемонаиха'
    elif 'волчих' in x:
        return 'волчиха'
    elif 'белокурих' in x:
        return 'белокуриха'
    elif 'поспелих' in x:
        return 'поспелиха'
    elif 'михайловск' in x:
        return 'михайловское'
    elif 'кулунда' in x:
        return 'кулунда'
    elif 'усть-каменогорск' in x:
        return 'усть-каменогорск'
    elif 'павлодар' in x:
        return 'павлодар'
    elif 'шипунов' in x:
        return 'шипуново'
    elif 'мамонтов' in x:
        return 'мамонтово'
    elif 'риддер' in x:
        return 'риддер'
    elif 'алтайское' in x:
        return 'алтайское'
    elif 'родин' in x:
        return 'родино'
    elif 'степное озер' in x:
        return 'степное озеро'
    elif 'томск' in x:
        return 'томск'
    elif 'топчих' in x:
        return 'топчиха'
    elif 'первомайск' in x:
        return 'первомайское'
    elif 'яров' in x:
        return 'яровое'
    elif 'сибирск' in x:
        return 'сибирский'
    elif 'троицк' in x:
        return 'троицкое'
    elif 'благовещенск' in x:
        return 'благовещенский'
    elif 'новичих' in x:
        return 'новичиха'
    elif 'налобих' in x:
        return 'налобиха'
    elif 'целинн' in x:
        return 'целинное'
    elif 'красногорск' in x:
        return 'красногорское'
    elif 'жалал-абад' in x:
        return 'жалал-абад'
    elif 'усть-калман' in x:
        return 'усть-калманка'
    elif 'залесов' in x:
        return 'залесово'
    elif 'ключ' in x:
        return 'ключи'
    elif 'тальменск' in x:
        return 'тальменский'
    elif 'курчатов' in x:
        return 'курчатов'
    else:
        return '0'

In [ ]:
test_df['Уч_Заведение_Город'] = test_df['Уч_Заведение_Город'].apply(add_city_learn)

In [ ]:
test_df['Уч_Заведение_Город'].value_counts().head(60)

барнаул             3392
0                   1553
бийск                276
горно-алтайск        106
новоалтайск          104
москва                94
славгород             73
камень-на-оби         72
рубцовск              70
заринск               67
павловск              56
первомайское          51
новосибирск           49
усть-каменогорск      49
риддер                47
шемонаиха             42
алейск                41
семей                 41
поспелиха             33
душанбе               27
шипуново              26
михайловское          25
белокуриха            24
топчиха               23
сибирский             22
томск                 21
яровое                21
тальменка             21
троицкое              21
благовещенский        20
мамонтово             19
павлодар              19
волчиха               19
целинное              19
ключи                 19
родино                18
тальменский           15
жалал-абад            14
залесово              14
алтайское             13


### Год_Окончания_УЗ

In [ ]:
df['Год_Окончания_УЗ'].value_counts()

2015.0    2056
2016.0    1990
2014.0    1986
2013.0    1696
2017.0    1220
2018.0     850
2012.0     685
2019.0     315
2011.0     209
2010.0     165
2008.0     126
2009.0     125
2006.0     110
2007.0      96
2005.0      83
2002.0      74
2003.0      74
2004.0      71
2001.0      52
2000.0      40
1999.0      35
1997.0      30
2020.0      28
1998.0      28
1996.0      23
1994.0      18
1995.0      17
1993.0      12
1991.0      12
1992.0      11
1988.0       7
1989.0       7
1985.0       7
1990.0       6
1984.0       5
1983.0       5
1987.0       4
1982.0       2
1980.0       1
1973.0       1
1974.0       1
1979.0       1
Name: Год_Окончания_УЗ, dtype: int64

In [ ]:
test_df['Год_Окончания_УЗ'].value_counts()

2014.0    1020
2015.0     991
2016.0     957
2013.0     857
2017.0     561
2018.0     435
2012.0     318
2019.0     169
2011.0     100
2010.0      80
2009.0      76
2008.0      66
2006.0      65
2007.0      54
2005.0      36
2002.0      34
2004.0      33
2001.0      28
2003.0      28
2000.0      20
2020.0      18
1995.0      16
1993.0      15
1999.0      14
1997.0      13
1996.0      11
1992.0      10
1998.0      10
1994.0       6
1990.0       6
1982.0       5
1981.0       3
1986.0       3
1987.0       3
1991.0       3
1988.0       2
1985.0       2
1989.0       2
1966.0       1
1983.0       1
1979.0       1
1984.0       1
Name: Год_Окончания_УЗ, dtype: int64

Заполним пропуски

In [ ]:
df['Год_Окончания_УЗ'] = df['Год_Окончания_УЗ'].fillna(0)

In [ ]:
test_df['Год_Окончания_УЗ'] = test_df['Год_Окончания_УЗ'].fillna(0)

In [ ]:
mode(list(df['Год_Окончания_УЗ'] - df['Год_Рождения']))

18.0

In [ ]:
mode(list(test_df['Год_Окончания_УЗ'] - test_df['Год_Рождения']))

18.0

Заполним пропуски, используя моду

In [ ]:
df.loc[df['Год_Окончания_УЗ'] == 0, 'Год_Окончания_УЗ'] = df['Год_Рождения'] + 18

In [ ]:
test_df.loc[test_df['Год_Окончания_УЗ'] == 0, 'Год_Окончания_УЗ'] = df['Год_Рождения'] + 18

Посмотрим получившиеся распределения

In [ ]:
fig = px.box(df, y="Год_Окончания_УЗ")
fig.show()

In [ ]:
fig = px.box(test_df, y="Год_Окончания_УЗ")
fig.show()

### Пособие

In [ ]:
df['Пособие'].value_counts()

0.0    12576
Name: Пособие, dtype: int64

In [ ]:
test_df['Пособие'].value_counts()

0.0    6207
Name: Пособие, dtype: int64

Видим, что в обоих датафреймах в столбце 'Пособие' присутствуют только нулевые значения. Удалим эту фичу

In [ ]:
df = df.drop('Пособие', axis=1)

In [ ]:
test_df = test_df.drop('Пособие', axis=1)

### Страна_ПП

Посмотрим страны на дублирующиеся значения

In [ ]:
df['Страна_ПП'].value_counts()

Россия                    12435
Казахстан                   415
Китай                       148
Таджикистан                 118
РОССИЯ                       37
Кыргызстан                   32
Киргизия                     21
Кыргызия                      6
Казахстан Респ                3
Казахстан респ                3
Росссия                       2
Кыргызская Республика         2
Армения                       2
Таджикистан Респ              2
Туркменистан                  2
Монголия                      2
Республика Таджикистан        1
Республика Казахстан          1
Казахстан ВКО                 1
Нигерия                       1
Франция                       1
Узбекистан                    1
Украина                       1
Name: Страна_ПП, dtype: int64

In [ ]:
df.loc[df['Страна_ПП'] == 'РОССИЯ', 'Страна_ПП'] = 'Россия'

In [ ]:
df.loc[df['Страна_ПП'] == 'Росссия', 'Страна_ПП'] = 'Россия'

In [ ]:
df.loc[df['Страна_ПП'] == 'Киргизия', 'Страна_ПП'] = 'Кыргызстан'

In [ ]:
df.loc[df['Страна_ПП'] == 'Кыргызия', 'Страна_ПП'] = 'Кыргызстан'

In [ ]:
df.loc[df['Страна_ПП'] == 'Казахстан Респ', 'Страна_ПП'] = 'Казахстан'

In [ ]:
df.loc[df['Страна_ПП'] == 'Казахстан респ', 'Страна_ПП'] = 'Казахстан'

In [ ]:
df.loc[df['Страна_ПП'] == 'Кыргызская Республика', 'Страна_ПП'] = 'Кыргызстан'

In [ ]:
df.loc[df['Страна_ПП'] == 'Республика Казахстан', 'Страна_ПП'] = 'Казахстан'

In [ ]:
df.loc[df['Страна_ПП'] == 'Таджикистан Респ', 'Страна_ПП'] = 'Таджикистан'

In [ ]:
df.loc[df['Страна_ПП'] == 'Республика Таджикистан', 'Страна_ПП'] = 'Таджикистан'

In [ ]:
df.loc[df['Страна_ПП'] == 'Казахстан ВКО', 'Страна_ПП'] = 'Казахстан'

А пропуски заполним 0

In [ ]:
df['Страна_ПП'] = df['Страна_ПП'].fillna('0')

Проделаем то же самое с тестовым набором данных

In [ ]:
test_df['Страна_ПП'].value_counts()

Россия                   6127
Казахстан                 194
Китай                      81
Таджикистан                42
РОССИЯ                     34
Кыргызстан                 20
Киргизия                   12
Узбекистан                  4
Кыргызская Республика       3
Казахстан респ              3
Кыргызия                    2
Казахстан Респ              2
Республика Казахстан        1
Монголия                    1
Казахстан ВКО               1
КИТАЙ                       1
КАЗАХСТАН                   1
Афганистан                  1
Туркменистан                1
Name: Страна_ПП, dtype: int64

In [ ]:
test_df.loc[test_df['Страна_ПП'] == 'РОССИЯ', 'Страна_ПП'] = 'Россия'

In [ ]:
test_df.loc[test_df['Страна_ПП'] == 'Киргизия', 'Страна_ПП'] = 'Кыргызстан'

In [ ]:
test_df.loc[test_df['Страна_ПП'] == 'Кыргызская Республика', 'Страна_ПП'] = 'Кыргызстан'

In [ ]:
test_df.loc[test_df['Страна_ПП'] == 'Казахстан респ', 'Страна_ПП'] = 'Казахстан'

In [ ]:
test_df.loc[test_df['Страна_ПП'] == 'Кыргызия', 'Страна_ПП'] = 'Кыргызстан'

In [ ]:
test_df.loc[test_df['Страна_ПП'] == 'Казахстан Респ', 'Страна_ПП'] = 'Казахстан'

In [ ]:
test_df.loc[test_df['Страна_ПП'] == 'Казахстан ВКО', 'Страна_ПП'] = 'Казахстан'

In [ ]:
test_df.loc[test_df['Страна_ПП'] == 'КАЗАХСТАН', 'Страна_ПП'] = 'Казахстан'

In [ ]:
test_df.loc[test_df['Страна_ПП'] == 'КИТАЙ', 'Страна_ПП'] = 'Китай'

In [ ]:
test_df.loc[test_df['Страна_ПП'] == 'Республика Казахстан', 'Страна_ПП'] = 'Казахстан'

In [ ]:
test_df['Страна_ПП'] = test_df['Страна_ПП'].fillna('0')

Посмотрим на распределения

In [ ]:
fig = px.histogram(df, x="Страна_ПП")
fig.show()

In [ ]:
fig = px.histogram(test_df, x="Страна_ПП")
fig.show()

### Регион_ПП

Посмотрим на дубликаты в столбце с регионом

In [ ]:
df['Регион_ПП'].value_counts()

Алтайский край                11492
Алтай Респ                      204
Республика Алтай                203
Восточно-Казахстанская обл      193
Кемеровская область              53
                              ...  
Баткенская область                1
Желал-Абадская обл                1
Магаданская Обл                   1
Джалал-Абадская                   1
Шэньси провинция                  1
Name: Регион_ПП, Length: 192, dtype: int64

Заполним пропуски 0

In [ ]:
df['Регион_ПП'] = df['Регион_ПП'].fillna('0')

Реализуем функцию для устранения дубликатов

In [ ]:
df['Регион_ПП'] = df['Регион_ПП'].apply(lambda x: x.lower())

In [ ]:
def add_reg(x):
    if 'алтай' in x:
        return 'алтай'
    elif 'казахстан' in x or 'вко' in x:
        return 'казахстан'
    elif 'кемеров' in x:
        return 'кемеровская'
    elif 'новосиб' in x:
        return 'новосибирск'
    elif 'павлодар' in x:
        return 'павлодарская'
    elif 'алайск' in x:
        return 'алайск'
    elif 'красноярск' in x:
        return 'красноярск'
    elif 'абадск' in x:
        return 'жалал-абадская'
    elif 'тыва' in x:
        return 'тыва'
    elif 'хатлонс' in x:
        return 'хатлонская'
    elif 'ляонин' in x:
        return 'ляонин'
    elif 'хайнан' in x:
        return 'хайнань'
    elif 'хэйлун' in x:
        return 'хэйлунцзян'
    else:
        return '0'

In [ ]:
df['Регион_ПП'] = df['Регион_ПП'].apply(add_reg)

In [ ]:
df['Регион_ПП'].value_counts()

алтай             11952
0                   882
казахстан           328
кемеровская          99
новосибирск          70
павлодарская         50
жалал-абадская       34
алайск               32
тыва                 28
красноярск           26
хэйлунцзян           25
хатлонская           24
хайнань              20
ляонин               14
Name: Регион_ПП, dtype: int64

Аналогично в тестовом датасете

In [ ]:
test_df['Регион_ПП'].value_counts()

Алтайский край                5722
Республика Алтай               100
Восточно-Казахстанская обл      79
Алтай Респ                      76
Кемеровская обл                 26
                              ... 
пров. Хубэй                      1
Гиссарский р-н                   1
Согдийская область               1
Дагестан респ                    1
Чуйская область                  1
Name: Регион_ПП, Length: 133, dtype: int64

In [ ]:
test_df['Регион_ПП'] = test_df['Регион_ПП'].fillna('0')

In [ ]:
test_df['Регион_ПП'] = test_df['Регион_ПП'].apply(lambda x: x.lower())

In [ ]:
def add_reg(x):
    if 'алтай' in x:
        return 'алтай'
    elif 'казахстан' in x or 'вко' in x:
        return 'казахстан'
    elif 'кемеров' in x:
        return 'кемеровская'
    elif 'новосиб' in x:
        return 'новосибирск'
    elif 'павлодар' in x:
        return 'павлодарская'
    elif 'алайск' in x:
        return 'алайск'
    elif 'красноярск' in x:
        return 'красноярск'
    elif 'абадск' in x:
        return 'жалал-абадская'
    elif 'тыва' in x:
        return 'тыва'
    elif 'хатлонс' in x:
        return 'хатлонская'
    elif 'ляонин' in x:
        return 'ляонин'
    elif 'хайнан' in x:
        return 'хайнань'
    elif 'хэйлун' in x:
        return 'хэйлунцзян'
    else:
        return '0'

In [ ]:
test_df['Регион_ПП'] = test_df['Регион_ПП'].apply(add_reg)

In [ ]:
test_df['Регион_ПП'].value_counts()

алтай             5912
0                  427
казахстан          155
кемеровская         48
новосибирск         37
тыва                19
алайск              18
красноярск          15
жалал-абадская      13
павлодарская        13
хайнань             10
хэйлунцзян           9
хатлонская           8
ляонин               7
Name: Регион_ПП, dtype: int64

### Город_ПП

Посомтрим на значения в столбце с городом

In [ ]:
df['Город_ПП'].value_counts()

Барнаул г         3735
г. Барнаул        1727
Барнаул           1174
Бийск г            246
Новоалтайск г      197
                  ... 
Марушка              1
с. Гилево            1
Чернышевский п       1
Кисилёвск г          1
Шила с               1
Name: Город_ПП, Length: 1765, dtype: int64

Заполним пропуски и применим реализованную ранее функцию для городов

In [ ]:
df['Город_ПП'] = df['Город_ПП'].fillna('0')

In [ ]:
df['Город_ПП'] = df['Город_ПП'].apply(lambda x: x.lower())

In [ ]:
df['Город_ПП'] = df['Город_ПП'].apply(add_city_learn)

In [ ]:
df['Город_ПП'].value_counts().head(60)

барнаул             6868
0                   3580
бийск                540
новоалтайск          398
рубцовск             190
камень-на-оби        181
славгород            132
заринск              129
горно-алтайск        113
алейск                93
семей                 92
белокуриха            89
павловск              86
сибирский             85
усть-каменогорск      62
тальменка             56
яровое                52
шипуново              49
троицкое              49
алтайское             48
волчиха               47
павлодар              47
шемонаиха             44
риддер                44
душанбе               42
поспелиха             38
новосибирск           37
ключи                 35
первомайское          33
мамонтово             31
кулунда               31
залесово              29
топчиха               26
михайловское          26
родино                25
степное озеро         25
целинное              24
красногорское         22
усть-калманка         21
новичиха              18


И в тестовом датасете

In [ ]:
test_df['Город_ПП'].value_counts()

Барнаул г            1872
г. Барнаул            879
Барнаул               575
Бийск г               120
г. Бийск               93
                     ... 
с. Степнной Кучук       1
Прокопьевск             1
Заводское с             1
Ананьевка с             1
Чемал                   1
Name: Город_ПП, Length: 1094, dtype: int64

In [ ]:
test_df['Город_ПП'] = test_df['Город_ПП'].fillna('0')

In [ ]:
test_df['Город_ПП'] = test_df['Город_ПП'].apply(lambda x: x.lower())

In [ ]:
test_df['Город_ПП'] = test_df['Город_ПП'].apply(add_city_learn)

In [ ]:
test_df['Город_ПП'].value_counts().head(60)

барнаул             3429
0                   1729
бийск                263
новоалтайск          192
рубцовск             105
камень-на-оби        102
славгород             65
заринск               62
горно-алтайск         54
алейск                46
сибирский             44
усть-каменогорск      38
павловск              38
белокуриха            38
семей                 37
риддер                33
тальменка             31
яровое                31
шемонаиха             21
троицкое              21
алтайское             20
ключи                 18
поспелиха             18
душанбе               18
первомайское          18
волчиха               18
кулунда               18
новосибирск           18
целинное              17
михайловское          16
родино                15
мамонтово             15
шипуново              13
залесово              13
топчиха               11
новичиха              11
павлодар              10
красногорское          9
степное озеро          8
курчатов               6


### Общежитие

In [ ]:
df['Общежитие'].value_counts()

0.0    10530
1.0     2968
Name: Общежитие, dtype: int64

Заполним пропуски 0

In [ ]:
df['Общежитие'] = df['Общежитие'].fillna(0)

И аналогично для тестового датасета

In [ ]:
test_df['Общежитие'].value_counts()

0.0    5169
1.0    1487
Name: Общежитие, dtype: int64

In [ ]:
test_df['Общежитие'] = test_df['Общежитие'].fillna(0)

### Наличие_Матери

Посмотрим, чтобы в столбце не было выбросов

In [ ]:
df['Наличие_Матери'].value_counts()

1    6948
0    6636
Name: Наличие_Матери, dtype: int64

In [ ]:
test_df['Наличие_Матери'].value_counts()

1    3354
0    3337
Name: Наличие_Матери, dtype: int64

### Наличие_Отца

Посмотрим, чтобы в столбце не было выбросов

In [ ]:
df['Наличие_Отца'].value_counts()

1.0    6922
0.0    6662
Name: Наличие_Отца, dtype: int64

In [ ]:
test_df['Наличие_Отца'].value_counts()

1.0    3350
0.0    3341
Name: Наличие_Отца, dtype: int64

### Страна_Родители

Посомтрим, есть ли дубликаты

In [ ]:
df['Страна_Родители'].value_counts()

Россия                    12239
Казахстан                   514
Китай                       147
Таджикистан                 133
Кыргызстан                   37
Киргизия                     31
Туркменистан                  5
Узбекистан                    3
Армения                       3
Кыргызская Республика         3
Республика Таджикистан        2
Монголия                      2
Республика Молдова            1
Нигерия                       1
Германия                      1
Республика Казахстан          1
казахстан                     1
Украина                       1
КНР                           1
Name: Страна_Родители, dtype: int64

Заполним дубли

In [ ]:
df.loc[df['Страна_Родители'] == 'Киргизия', 'Страна_Родители'] = 'Кыргызстан'

In [ ]:
df.loc[df['Страна_Родители'] == 'Кыргызская Республика', 'Страна_Родители'] = 'Кыргызстан'

In [ ]:
df.loc[df['Страна_Родители'] == 'Республика Таджикистан', 'Страна_Родители'] = 'Таджикистан'

In [ ]:
df.loc[df['Страна_Родители'] == 'казахстан', 'Страна_Родители'] = 'Казахстан'

In [ ]:
df.loc[df['Страна_Родители'] == 'Республика Казахстан', 'Страна_Родители'] = 'Казахстан'

In [ ]:
df['Страна_Родители'] = df['Страна_Родители'].fillna('0')

И проделаем аналогичную работу для тестового датасета

In [ ]:
test_df['Страна_Родители'].value_counts()

Россия                    6073
Казахстан                  239
Китай                       82
Таджикистан                 45
Кыргызстан                  24
Киргизия                    14
Кыргызская Республика        3
Узбекистан                   3
Афганистан                   2
РОССИЯ                       2
Туркменистан                 2
Монголия                     1
Республика Таджикистан       1
Чеченская республика         1
Кыргызия                     1
Name: Страна_Родители, dtype: int64

In [ ]:
test_df.loc[test_df['Страна_Родители'] == 'Киргизия', 'Страна_Родители'] = 'Кыргызстан'

In [ ]:
test_df.loc[test_df['Страна_Родители'] == 'Кыргызская Республика', 'Страна_Родители'] = 'Кыргызстан'

In [ ]:
test_df.loc[test_df['Страна_Родители'] == 'РОССИЯ', 'Страна_Родители'] = 'Россия'

In [ ]:
test_df.loc[test_df['Страна_Родители'] == 'Республика Таджикистан', 'Страна_Родители'] = 'Таджикистан'

In [ ]:
test_df.loc[test_df['Страна_Родители'] == 'Кыргызия', 'Страна_Родители'] = 'Кыргызстан'

In [ ]:
test_df['Страна_Родители'] = test_df['Страна_Родители'].fillna('0')

### Опекунство

Проверим, есть ли в столбце Опекунство выбросы

In [ ]:
df['Опекунство'].value_counts()

0.0    13578
1.0        6
Name: Опекунство, dtype: int64

In [ ]:
test_df['Опекунство'].value_counts()

0.0    6685
1.0       6
Name: Опекунство, dtype: int64

### Село

Посмотрим, есть ли выбросы

In [ ]:
df['Село'].value_counts()

0.0    10401
1.0     3097
Name: Село, dtype: int64

Заполним пропуски 0

In [ ]:
df['Село'] = df['Село'].fillna(0)

И для тестового датасета проделаем аналогичную работу

In [ ]:
test_df['Село'].value_counts()

0.0    5170
1.0    1484
Name: Село, dtype: int64

In [ ]:
test_df['Село'] = test_df['Село'].fillna(0)

### Иностранец


И для столбца Иностранец найдём наиболее часто встречающееся значение и им заполним пропуски в обоих датасетах

In [ ]:
df['Иностранец'].value_counts()

0.0    12337
1.0      937
Name: Иностранец, dtype: int64

In [ ]:
df['Иностранец'] = df['Иностранец'].fillna(0)

In [ ]:
test_df['Иностранец'].value_counts()

0.0    6095
1.0     466
Name: Иностранец, dtype: int64

In [ ]:
test_df['Иностранец'] = test_df['Иностранец'].fillna(0)

### КодФакультета

Посмотрим, какие значения встречаются в столбце с кодом факультета

In [ ]:
df['КодФакультета'].value_counts()

26.0    2776
25.0    2171
41.0    1485
51.0    1109
34.0     960
24.0     692
27.0     679
28.0     662
31.0     622
35.0     547
40.0     471
36.0     447
30.0     435
48.0     234
45.0      91
47.0      84
49.0      76
46.0      26
53.0      15
37.0       2
Name: КодФакультета, dtype: int64

Приведём к типу int

In [ ]:
df['КодФакультета'] = df['КодФакультета'].astype(int)

Посмотрим на распределение

In [ ]:
fig = px.histogram(df, x="КодФакультета")
fig.show()

Сделаем аналогичную работу для теста

In [ ]:
test_df['КодФакультета'].value_counts()

26.0    1335
25.0    1060
41.0     741
51.0     550
34.0     456
27.0     384
24.0     356
28.0     314
31.0     280
35.0     275
40.0     223
36.0     220
30.0     211
48.0     114
47.0      60
45.0      50
49.0      41
46.0      16
53.0       4
37.0       1
Name: КодФакультета, dtype: int64

In [ ]:
test_df['КодФакультета'] = test_df['КодФакультета'].astype(int)

In [ ]:
fig = px.histogram(test_df, x="КодФакультета")
fig.show()

### СрБаллАттестата

Посмотрим, какие значения встречаются в столбце со средним баллом

In [ ]:
df['СрБаллАттестата'].describe()

count    13584.000000
mean        73.223274
std        258.045027
min          0.000000
25%         47.000000
50%         61.000000
75%         75.000000
max       5000.000000
Name: СрБаллАттестата, dtype: float64

In [ ]:
fig = px.box(df, y="СрБаллАттестата")
fig.show()

In [ ]:
test_df['СрБаллАттестата'].describe()

count    6691.000000
mean       71.681369
std       250.386989
min         0.000000
25%        47.000000
50%        61.000000
75%        76.000000
max      7232.000000
Name: СрБаллАттестата, dtype: float64

In [ ]:
fig = px.box(test_df, y="СрБаллАттестата")
fig.show()

Значения в столбце делятся на два типа: средний балл аттестата и средний балл егэ. Создадим для них разные столбцы, а все неподходящие значения заменим 0

In [ ]:
df['СрБаллЕГЭ'] = df['СрБаллАттестата'].copy()

In [ ]:
df.loc[df['СрБаллАттестата'] > 5, 'СрБаллАттестата'] = 0

In [ ]:
df.loc[df['СрБаллАттестата'] < 2, 'СрБаллАттестата'] = 0

In [ ]:
df.loc[df['СрБаллЕГЭ'] > 100, 'СрБаллЕГЭ'] = 0

In [ ]:
df.loc[df['СрБаллЕГЭ'] < 30, 'СрБаллЕГЭ'] = 0

Аналогично в тестовом датасете

In [ ]:
test_df['СрБаллЕГЭ'] = test_df['СрБаллАттестата'].copy()

In [ ]:
test_df.loc[test_df['СрБаллАттестата'] > 5, 'СрБаллАттестата'] = 0

In [ ]:
test_df.loc[test_df['СрБаллАттестата'] < 2, 'СрБаллАттестата'] = 0

In [ ]:
test_df.loc[test_df['СрБаллЕГЭ'] > 100, 'СрБаллЕГЭ'] = 0

In [ ]:
test_df.loc[test_df['СрБаллЕГЭ'] < 30, 'СрБаллЕГЭ'] = 0

## Выделим выборки

In [ ]:
X = df.drop('Статус', axis = 1)
y = df["Статус"]

In [ ]:
X.shape

(13584, 27)

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=42)

## Обучение модели

Возьмём модель CatBoost, поскольку она работает с категориальными фичами

In [ ]:
cat_features = ['Код_группы', 'Основания', 'Пол', 'Изучаемый_Язык', 'Уч_Заведение', 'Где_Находится_УЗ', 'Страна_ПП', 'Регион_ПП', 'Город_ПП', 'Страна_Родители', 'Уч_Заведение_Тип', 'Уч_Заведение_Город']

In [ ]:
df[cat_features] = df[cat_features].astype(str)

Сделаем классы балансированными

In [ ]:
classes = np.unique(y_train)
weights = compute_class_weight(class_weight='balanced', classes=classes, y=y_train)
class_weights = dict(zip(classes, weights))

In [ ]:
cat_model = CatBoostClassifier(loss_function='MultiClassOneVsAll', iterations=1001, depth=10, verbose=10, cat_features=cat_features,  class_weights=class_weights)
cat_model.fit(X_train, y_train)

0:	learn: 0.6845481	total: 566ms	remaining: 9m 26s
10:	learn: 0.6129705	total: 3.11s	remaining: 4m 39s
20:	learn: 0.5459555	total: 7.37s	remaining: 5m 43s
30:	learn: 0.4991537	total: 11.2s	remaining: 5m 51s
40:	learn: 0.4661356	total: 15.4s	remaining: 5m 59s
50:	learn: 0.4432036	total: 18.8s	remaining: 5m 50s
60:	learn: 0.4183648	total: 23.8s	remaining: 6m 7s
70:	learn: 0.3985862	total: 28.5s	remaining: 6m 13s
80:	learn: 0.3831752	total: 32.9s	remaining: 6m 14s
90:	learn: 0.3706732	total: 36.8s	remaining: 6m 7s
100:	learn: 0.3603066	total: 41.1s	remaining: 6m 6s
110:	learn: 0.3503525	total: 45.9s	remaining: 6m 7s
120:	learn: 0.3408460	total: 50.4s	remaining: 6m 6s
130:	learn: 0.3330872	total: 56.1s	remaining: 6m 12s
140:	learn: 0.3261977	total: 1m	remaining: 6m 11s
150:	learn: 0.3198477	total: 1m 8s	remaining: 6m 24s
160:	learn: 0.3142865	total: 1m 13s	remaining: 6m 23s
170:	learn: 0.3087847	total: 1m 19s	remaining: 6m 24s
180:	learn: 0.3027408	total: 1m 25s	remaining: 6m 25s
190:	lear

In [ ]:
predictions_cat = cat_model.predict(X_test)
f1 = f1_score(y_test, predictions_cat, average='macro') 
f1

0.7348739922213124

Посомтрим, какие фичи оказались наиболее значимыми

In [ ]:
cat_model.get_feature_importance(prettified=True)

Feature Id  Importances
0           Код_группы    23.703200
1            Основания    11.047582
2            СрБаллЕГЭ     5.919023
3                   ID     5.464438
4        КодФакультета     5.213537
5         Уч_Заведение     4.607536
6                  Пол     4.506639
7     Где_Находится_УЗ     4.343756
8         Год_Рождения     4.337404
9     Уч_Заведение_Тип     4.272261
10      Число_Рождения     4.183950
11            Город_ПП     3.526436
12     Год_Поступления     3.194630
13      Месяц_Рождения     3.124620
14  Уч_Заведение_Город     2.656659
15    Год_Окончания_УЗ     2.340333
16      Изучаемый_Язык     2.268598
17           Регион_ПП     1.176540
18     Страна_Родители     1.060076
19           Страна_ПП     0.724932
20      Наличие_Матери     0.642713
21        Наличие_Отца     0.642024
22     СрБаллАттестата     0.533053
23                Село     0.306303
24           Общежитие     0.182545
25          Иностранец     0.021068
26          Опекунство     0.000145

## Обучение на всей выборке

In [ ]:
classes = np.unique(y)
weights = compute_class_weight(class_weight='balanced', classes=classes, y=y)
class_weights = dict(zip(classes, weights))

cat_features_l = ['Код_группы','Основания', 'Пол', 'Изучаемый_Язык', 'Уч_Заведение', 'Где_Находится_УЗ', 'Страна_ПП', 'Регион_ПП', 'Город_ПП', 'Страна_Родители', 'Уч_Заведение_Тип', 'Уч_Заведение_Город']
X[cat_features_l] = X[cat_features_l].astype(str)
cat_model_l = CatBoostClassifier(loss_function='MultiClassOneVsAll', iterations=1001, depth=10, verbose=10, cat_features=cat_features,  class_weights=class_weights)
cat_model_l.fit(X, y)

0:	learn: 0.6841675	total: 568ms	remaining: 9m 28s
10:	learn: 0.5988837	total: 4s	remaining: 6m
20:	learn: 0.5304613	total: 7.82s	remaining: 6m 4s
30:	learn: 0.4815370	total: 13.1s	remaining: 6m 50s
40:	learn: 0.4481144	total: 17.2s	remaining: 6m 43s
50:	learn: 0.4228799	total: 22.6s	remaining: 7m 1s
60:	learn: 0.4037039	total: 27.6s	remaining: 7m 5s
70:	learn: 0.3881206	total: 32.1s	remaining: 7m
80:	learn: 0.3720780	total: 36.4s	remaining: 6m 53s
90:	learn: 0.3586754	total: 41.2s	remaining: 6m 52s
100:	learn: 0.3489139	total: 46.3s	remaining: 6m 52s
110:	learn: 0.3392513	total: 51.1s	remaining: 6m 49s
120:	learn: 0.3323942	total: 55.8s	remaining: 6m 46s
130:	learn: 0.3231256	total: 1m 1s	remaining: 6m 47s
140:	learn: 0.3171615	total: 1m 6s	remaining: 6m 47s
150:	learn: 0.3122005	total: 1m 12s	remaining: 6m 46s
160:	learn: 0.3065684	total: 1m 18s	remaining: 6m 47s
170:	learn: 0.3013379	total: 1m 24s	remaining: 6m 48s
180:	learn: 0.2977631	total: 1m 28s	remaining: 6m 42s
190:	learn: 0.

In [ ]:
test_df[cat_features_l] = test_df[cat_features_l].astype(str)

df_test_pred = cat_model_l.predict(test_df)

## Cоздание файла с ответом

In [ ]:
df_sub = pd.read_csv('/content/sample_submission.csv')

In [ ]:
df_sub

ID  Статус
0     64996     NaN
1     71837     NaN
2     86587     NaN
3     73673     NaN
4     54709     NaN
...     ...     ...
6686  74342     NaN
6687  54876     NaN
6688  66879     NaN
6689  64982     NaN
6690  69975     NaN

[6691 rows x 2 columns]

In [ ]:
df_sub["Статус"] = df_test_pred
df_sub.head(4)

ID  Статус
0  64996       4
1  71837       4
2  86587       3
3  73673       3

In [ ]:
df_sub.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6691 entries, 0 to 6690
Data columns (total 2 columns):
 #   Column  Non-Null Count  Dtype
---  ------  --------------  -----
 0   ID      6691 non-null   int64
 1   Статус  6691 non-null   int64
dtypes: int64(2)
memory usage: 104.7 KB


In [ ]:
df_sub.to_csv("/content/submission.csv", index = False)